In [1]:
# To reload external files automatically (ex: utils)
%load_ext autoreload
%autoreload 2  

import numpy as np
import pandas as pd
import netCDF4 as nc
from netCDF4 import Dataset
import matplotlib.pyplot as plt
import xarray as xr
from scipy import stats
import pymannkendall as mk  

In [2]:
# For parallelisation 
from dask.distributed import Client
client = Client(n_workers=16, threads_per_worker=2, memory_limit='32GB')
client

C:\Users\Hamid\anaconda3\lib\site-packages\distributed\node.py:180: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 53170 instead
  warnings.warn(


<Client: 'tcp://127.0.0.1:53171' processes=16 threads=32, memory=476.84 GiB>

In [3]:
period = slice('1982-01-01', '2014-12-31')
mons= [1,2,3,4,11,12]
months_labels = ["JAN","FEB","MAR","APR","NOV","DEC"] 
output_path = r'C:\Users\Hamid\Desktop\results\trends\ERA_LAND'              
path_era_land = r'C:\Data\Snow\SCFG\Reanalysis\monthly_values'

In [4]:
scf_monthly_value_era_land_9km = xr.open_dataset(path_era_land + r'\scf_ERA_Land_1950_2022_variables_monthly_values.nc').sel(time=period).load()

In [5]:
# We initialize a list of parameters names that will be served to acess the data for each parameter
parameters = ['scf_monthly_value', 'days_with_snow', 'ext_days_with_snow', 'scf_monthly_value_15', 'days_with_snow_15', 'ext_days_with_snow_15', ]

In [6]:
trend_era_land = {parameters[i]:pd.DataFrame(columns=['month', 'lat', 'lon', parameters[i]+'_slope', parameters[i]+'_p']) for i in range(6)}  
df = pd.DataFrame(columns=['month', 'lat', 'lon', 'slope', 'p'])  

lats = scf_monthly_value_era_land_9km.lat.values
lons = scf_monthly_value_era_land_9km.lon.values

n = len(lats)*len(lons)*6*6

ctr = 0
i=0
for var in parameters:
    slope = []  
    p = []   
    la = []   
    lo = []   
    mons = []
    slope=[]
    p=[]
    for mon in [1,2,3,4,11,12]:
        for lat in lats:
            for lon in lons:
                print(ctr/n*100)
                ctr=ctr+1
                try:
                    trend = mk.original_test(scf_monthly_value_era_land_9km.groupby('time.month')[mon].loc[{'lat':lat,'lon':lon}][var].values)
                    slope.append(trend.slope)
                    p.append(trend.p)
                    la.append(lat)
                    lo.append(lon)
                    mons.append(mon)   
                
                except ZeroDivisionError:
                    continue 
                    
    trend_era_land[var]['month'] = mons
    trend_era_land[var][parameters[i]+'_slope'] = slope
    trend_era_land[var][parameters[i]+'_p'] = p
    trend_era_land[var]['lat'] = la
    trend_era_land[var]['lon'] = lo
    
    i=i+1
    

0.0
0.0006724226041582614
0.0013448452083165228
0.002017267812474784
0.0026896904166330456
0.003362113020791307
0.004034535624949568
0.00470695822910783
0.005379380833266091
0.0060518034374243525
0.006724226041582614
0.007396648645740875
0.008069071249899137
0.008741493854057397
0.00941391645821566
0.01008633906237392
0.010758761666532182
0.011431184270690443
0.012103606874848705
0.012776029479006967
0.013448452083165228
0.01412087468732349
0.01479329729148175
0.015465719895640013
0.016138142499798273
0.016810565103956534
0.017482987708114794
0.01815541031227306
0.01882783291643132
0.01950025552058958
0.02017267812474784
0.020845100728906104
0.021517523333064364
0.022189945937222625
0.022862368541380886
0.023534791145539146
0.02420721374969741
0.02487963635385567
0.025552058958013935
0.02622448156217219
0.026896904166330456
0.027569326770488716
0.02824174937464698
0.028914171978805237
0.0295865945829635
0.03025901718712176
0.030931439791280026
0.03160386239543828
0.03227628499959655
0.

In [7]:
trend_era_land

{'scf_monthly_value':        month   lat       lon  scf_monthly_value_slope  scf_monthly_value_p
 0          1  35.0 -6.200012                      0.0             1.000000
 1          1  35.0 -6.099976                      0.0             1.000000
 2          1  35.0 -6.000000                      0.0             1.000000
 3          1  35.0 -5.900024                      0.0             1.000000
 4          1  35.0 -5.799988                      0.0             1.000000
 ...      ...   ...       ...                      ...                  ...
 20341     12  30.0 -2.400024                      0.0             1.000000
 20342     12  30.0 -2.299988                      0.0             0.958122
 20343     12  30.0 -2.200012                      0.0             0.958122
 20344     12  30.0 -2.099976                      0.0             0.958122
 20345     12  30.0 -2.000000                      0.0             0.958122
 
 [20346 rows x 5 columns],
 'days_with_snow':        month   lat 

In [8]:
for p in parameters:
    trend_era_land[p].set_index(['month','lon','lat']).to_xarray().to_netcdf(output_path +'/ERA_LAND_'+p+'_trend.nc')